In [25]:
import re
import numpy as np
import pandas as pd
from pprint import pprint
 
# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
 
# Enable logging for gensim - optional
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
 
# Plotting tools
import pyLDAvis
import pyLDAvis.gensim # don't skip this
import matplotlib.pyplot as plt
%matplotlib inline
    
import warnings
warnings.filterwarnings("ignore",category=DeprecationWarning)

In [3]:
# 명사 파일 로드

data=pd.read_excel('/home/ekim_reverse/PyCode/study/Python.study/toy_project/data_pos_nva.xlsx')

In [4]:
# 컬럼확인

data.columns

Index(['c_n_pos_a', 'c_n_pos_v', 'c_n_pos_n_more1', 'c_n_pos_n_more2',
       't_n_pos_a', 't_n_pos_v'],
      dtype='object')

In [5]:
# 빈도 수 2개 이하는 제거한 명사만 추출

data_n=data['c_n_pos_n_more2']

In [6]:
# 결측치 제거

data_n=data_n.dropna(axis=0)

In [7]:
# 확인

data_n

0         반도체
1          전자
2          기업
3          시장
4          사업
         ... 
46236     중재위
46237      광초
46238     사할린
46239    간접흡연
46240      필순
Name: c_n_pos_n_more2, Length: 46241, dtype: object

In [8]:
# 리스트로 변환

data_nl=data_n.tolist()

In [9]:
# 확인

data_nl

['반도체',
 '전자',
 '기업',
 '시장',
 '사업',
 '기술',
 '삼성',
 '투자',
 '산업',
 '중국',
 '수출',
 '업체',
 '실적',
 '개발',
 '증가',
 '한국',
 '생산',
 '이익',
 '영업',
 '지난해',
 '제품',
 '매출',
 '세계',
 '올해',
 '전망',
 '미국',
 '대비',
 '기록',
 '성장',
 '지난',
 '국내',
 '감소',
 '분야',
 '증권',
 '규모',
 '하락',
 '부문',
 '상승',
 '대한',
 '그룹',
 '자동차',
 '최근',
 '통해',
 '확대',
 '위해',
 '때문',
 '디스플레이',
 '관련',
 '예상',
 '글로벌',
 '회사',
 '주가',
 '장비',
 '스마트폰',
 '이번',
 '이후',
 '계획',
 '정부',
 '개선',
 '경제',
 '공장',
 '회장',
 '현재',
 '이상',
 '연구원',
 '대표',
 '발표',
 '하이닉스',
 '업종',
 '수준',
 '지원',
 '업계',
 '최대',
 '부품',
 '분석',
 '가격',
 '시스템',
 '기자',
 '공급',
 '전략',
 '수요',
 '대해',
 '경우',
 '종목',
 '바이오',
 '예정',
 '일본',
 '설명',
 '판매',
 '상황',
 '단지',
 '가장',
 '인수',
 '달러',
 '기준',
 '지수',
 '공정',
 '우리',
 '거래',
 '지속',
 '메모리',
 '지역',
 '서비스',
 '라며',
 '경쟁력',
 '모바일',
 '갤럭시',
 '목표',
 '협력',
 '영향',
 '미래',
 '평가',
 '매수',
 '사장',
 '관계자',
 '기존',
 '서울',
 '전체',
 '각각',
 '건설',
 '평택',
 '진행',
 '유지',
 '중심',
 '소재',
 '해외',
 '연구',
 '시작',
 '혁신',
 '효과',
 '센터',
 '가능성',
 '문제',
 '주요',
 '사용',
 '나노',
 '확보',
 '경기',
 '경쟁',
 '의견',

In [10]:
# 뉴스 파일 로드

data_all=pd.read_excel('/home/ekim_reverse/PyCode/study/Python.study/toy_project/online_news_nosw.xlsx')

In [11]:
# n_pos_t 리스트안의 문자형 분리 & 특수문자 제거

data_sp=[]
for i in range(len(data)):
    data_sp.append(data_all['c_n_pos'][i].split(','))
    
data_sp[0]

["['공동'",
 " '스틸'",
 " '국적'",
 " '플레이'",
 " '개시'",
 " '전량'",
 " '신하우'",
 " '장치'",
 " '자금'",
 " '허브'",
 " '방식'",
 " '에이'",
 " '터보'",
 " '관련'",
 " '신청'",
 " '볼팅'",
 " '보호'",
 " '시스템'",
 " '배정'",
 " '합병'",
 " '지방법원'",
 " '실권'",
 " '규모'",
 " '테크'",
 " '보통주'",
 " '시설'",
 " '만료'",
 " '최대'",
 " '덕통'",
 " '위해'",
 " '매각'",
 " '유동성'",
 " '예비'",
 " '퇴임'",
 " '마련'",
 " '증권'",
 " '중앙'",
 " '흡수'",
 " '실사'",
 " '건설'",
 " '협상'",
 " '유상증자'",
 " '월드'",
 " '체제'",
 " '중도'",
 " '확보'",
 " '자회사'",
 " '멀티캐스트'",
 " '기업'",
 " '보유'",
 " '반도체'",
 " '대표'",
 " '처분'",
 " '주주'",
 " '열사'",
 " '미래에셋'",
 " '사외이사'",
 " '절차'",
 " '앤리'",
 " '회생'",
 " '와이드'",
 " '변경'",
 " '특허'",
 " '엔터테인먼트'",
 " '네트워크'",
 " '취득'",
 " '제철'",
 " '자동'",
 " '홀딩스'",
 " '결정']"]

In [12]:
data_st=[]
for i in range(len(data_sp)):
    data_st2=[]
    for j in data_sp[i]:
        data_st2.append(j.lstrip('[').rstrip('"]').strip(" ' "))
    data_st.append(data_st2)

data_st[0][1]

'스틸'

In [13]:
# data_nl을 세트로 변환

a=set(data_nl)

In [14]:
# 명사파일로 필터링하여 n_pos_t 컬럼의 명사만 추출

SW_del=[]
for i in data_st:
    b=set(i)
    SW_del.append(b&a)

In [15]:
# 확인

SW_del

[{'개시',
  '건설',
  '결정',
  '공동',
  '관련',
  '국적',
  '규모',
  '기업',
  '네트워크',
  '대표',
  '덕통',
  '마련',
  '만료',
  '매각',
  '멀티캐스트',
  '미래에셋',
  '반도체',
  '방식',
  '배정',
  '변경',
  '보유',
  '보통주',
  '보호',
  '볼팅',
  '사외이사',
  '스틸',
  '시설',
  '시스템',
  '신청',
  '실권',
  '실사',
  '앤리',
  '에이',
  '엔터테인먼트',
  '열사',
  '예비',
  '와이드',
  '월드',
  '위해',
  '유동성',
  '유상증자',
  '자금',
  '자동',
  '자회사',
  '장치',
  '전량',
  '절차',
  '제철',
  '주주',
  '중도',
  '중앙',
  '증권',
  '지방법원',
  '처분',
  '체제',
  '최대',
  '취득',
  '터보',
  '테크',
  '퇴임',
  '특허',
  '플레이',
  '합병',
  '허브',
  '협상',
  '홀딩스',
  '확보',
  '회생',
  '흡수'},
 {'가전',
  '개막',
  '경쟁',
  '공간',
  '관심',
  '교통',
  '구분',
  '구해',
  '기능',
  '기술',
  '내장',
  '뉴스',
  '달라',
  '대화',
  '드라마',
  '라스베거스',
  '라스베이거스',
  '명령',
  '무려',
  '무인',
  '미국',
  '미래',
  '반도체',
  '반응',
  '보도',
  '비롯',
  '상용',
  '샌프란시스코',
  '생활',
  '세계',
  '소개',
  '손목',
  '수단',
  '스마트워치',
  '시계',
  '시스템',
  '연상',
  '영상',
  '영상편집',
  '외치',
  '운전자',
  '원리',
  '위치',
  '위험',
  '음성',
  '의미',
  '인식',
  '일상생활',
  '자동차',
  '잡지',

In [ ]:
# 데이터프레임으로 변경

# s_w_del=pd.DataFrame(SW_del)

In [ ]:
# 엑셀 저장

#s_w_del.to_excel('C:\\Users\\LENOVO\\online_news_ns2.xlsx',index=False)

In [16]:
# set을 리스트로 변환

SW_del=list(SW_del)

In [17]:
# 사전 생성

id2word = corpora.Dictionary(SW_del)

In [18]:
# 말뭉치 생성

texts = SW_del

In [19]:
# Term Document Frequency

corpus = [id2word.doc2bow(text) for text in texts]

In [20]:
# 확인
print(corpus[0])

[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1), (23, 1), (24, 1), (25, 1), (26, 1), (27, 1), (28, 1), (29, 1), (30, 1), (31, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (37, 1), (38, 1), (39, 1), (40, 1), (41, 1), (42, 1), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1), (48, 1), (49, 1), (50, 1), (51, 1), (52, 1), (53, 1), (54, 1), (55, 1), (56, 1), (57, 1), (58, 1), (59, 1), (60, 1), (61, 1), (62, 1), (63, 1), (64, 1), (65, 1), (66, 1), (67, 1), (68, 1)]


In [21]:
# 빈도수 표시

[[(id2word[id], freq) for id, freq in cp] for cp in corpus]

[[('개시', 1),
  ('건설', 1),
  ('결정', 1),
  ('공동', 1),
  ('관련', 1),
  ('국적', 1),
  ('규모', 1),
  ('기업', 1),
  ('네트워크', 1),
  ('대표', 1),
  ('덕통', 1),
  ('마련', 1),
  ('만료', 1),
  ('매각', 1),
  ('멀티캐스트', 1),
  ('미래에셋', 1),
  ('반도체', 1),
  ('방식', 1),
  ('배정', 1),
  ('변경', 1),
  ('보유', 1),
  ('보통주', 1),
  ('보호', 1),
  ('볼팅', 1),
  ('사외이사', 1),
  ('스틸', 1),
  ('시설', 1),
  ('시스템', 1),
  ('신청', 1),
  ('실권', 1),
  ('실사', 1),
  ('앤리', 1),
  ('에이', 1),
  ('엔터테인먼트', 1),
  ('열사', 1),
  ('예비', 1),
  ('와이드', 1),
  ('월드', 1),
  ('위해', 1),
  ('유동성', 1),
  ('유상증자', 1),
  ('자금', 1),
  ('자동', 1),
  ('자회사', 1),
  ('장치', 1),
  ('전량', 1),
  ('절차', 1),
  ('제철', 1),
  ('주주', 1),
  ('중도', 1),
  ('중앙', 1),
  ('증권', 1),
  ('지방법원', 1),
  ('처분', 1),
  ('체제', 1),
  ('최대', 1),
  ('취득', 1),
  ('터보', 1),
  ('테크', 1),
  ('퇴임', 1),
  ('특허', 1),
  ('플레이', 1),
  ('합병', 1),
  ('허브', 1),
  ('협상', 1),
  ('홀딩스', 1),
  ('확보', 1),
  ('회생', 1),
  ('흡수', 1)],
 [('반도체', 1),
  ('시스템', 1),
  ('최대', 1),
  ('가전', 1),
  ('개막', 1),
  ('경쟁', 1

In [22]:
# LDA 모델 생성

lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus,
id2word=id2word,
num_topics=40,
random_state=100,
update_every=1,
chunksize=100,
passes=10,
alpha='auto',
per_word_topics=True)

In [23]:
# 40개의 토픽 출력

pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

[(6,
  '0.000*"사스" + 0.000*"통일신라" + 0.000*"거름" + 0.000*"동년" + 0.000*"배설물" + '
  '0.000*"분립" + 0.000*"인겔" + 0.000*"최치원" + 0.000*"권영근" + 0.000*"역구"'),
 (36,
  '0.183*"프리" + 0.170*"닉스" + 0.125*"스틸" + 0.103*"시멘트" + 0.081*"파이" + '
  '0.030*"샤프" + 0.021*"공주" + 0.019*"타이완" + 0.018*"낸셜" + 0.008*"혼하"'),
 (11,
  '0.225*"과학" + 0.175*"측정" + 0.088*"왼쪽" + 0.082*"압력" + 0.059*"표준" + 0.051*"경력" '
  '+ 0.048*"인물" + 0.036*"직류" + 0.031*"명예" + 0.023*"상해"'),
 (35,
  '0.294*"뉴스" + 0.132*"피해" + 0.058*"체인지" + 0.049*"머징" + 0.048*"변동" + '
  '0.047*"현물" + 0.039*"가격" + 0.038*"보합" + 0.037*"제품" + 0.036*"평균"'),
 (26,
  '0.229*"조명" + 0.191*"공업" + 0.162*"홍보" + 0.146*"진흥" + 0.068*"복지" + 0.065*"보관" '
  '+ 0.037*"전제" + 0.005*"구지원" + 0.000*"영상" + 0.000*"통일신라"'),
 (29,
  '0.185*"특수" + 0.094*"전자기기" + 0.065*"지출" + 0.059*"접촉" + 0.056*"공기" + '
  '0.055*"제거" + 0.054*"프로" + 0.053*"필터" + 0.051*"누리" + 0.051*"검색"'),
 (3,
  '0.199*"보도" + 0.149*"퀄컴" + 0.111*"저작권" + 0.083*"해상도" + 0.075*"초고" + '
  '0.065*"화질" + 0.052*"화면" + 0.036*"체감" +

In [26]:
# Visualize the topics

pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)
vis

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
25     0.220786 -0.158885       1        1  13.165530
23     0.218773  0.077535       2        1  12.359402
30     0.195396  0.160956       3        1   8.025303
20     0.154335 -0.001996       4        1   7.709163
7      0.112438  0.109427       5        1   7.435936
15     0.154219  0.098437       6        1   6.910157
1      0.177946  0.191838       7        1   6.585859
14     0.144146  0.101655       8        1   4.117937
2      0.178709 -0.132295       9        1   3.241841
31     0.121802 -0.283344      10        1   3.092795
32     0.124949 -0.075688      11        1   2.783530
38     0.063040  0.174521      12        1   2.421584
12     0.003798 -0.026934      13        1   1.911006
4      0.053102 -0.124039      14        1   1.794620
39     0.070032  0.001878      15        1   1.771498
21     0.123057 -0.223151      16        1   1.640077
18     0.132266  0.117126      17        1   1.542295
24     0.019930 -0.086134      18        1   1.284207
34    -0.054063  0.012992      19        1   1.135383
9     -0.039217  0.003786      20        1   1.099421
16    -0.045542  0.071189      21        1   1.009113
37     0.040913 -0.015521      22        1   0.978333
10    -0.063319  0.040870      23        1   0.957362
33    -0.078895  0.016955      24        1   0.799865
0     -0.024526  0.039967      25        1   0.706803
28    -0.090166  0.003447      26        1   0.658180
17    -0.093386  0.009757      27        1   0.588682
27    -0.086843 -0.037372      28        1   0.519693
5     -0.112842 -0.003967      29        1   0.513438
8     -0.099848  0.013124      30        1   0.484924
22    -0.117802  0.010700      31        1   0.453296
19    -0.122859  0.006821      32        1   0.440743
13    -0.060762 -0.147969      33        1   0.412703
3     -0.146295  0.013727      34        1   0.319490
29    -0.145380  0.020604      35        1   0.286996
26    -0.162812  0.010065      36        1   0.248780
35    -0.106217 -0.022171      37        1   0.245711
11    -0.170269  0.019776      38        1   0.237579
36    -0.223836  0.001162      39        1   0.108608
6     -0.264757  0.011150      40        1   0.002159, topic_info=        Term          Freq         Total Category  logprob  loglift
16       반도체  74374.000000  74374.000000  Default  30.0000  30.0000
600       제품  19001.000000  19001.000000  Default  29.0000  29.0000
304       투자  26150.000000  26150.000000  Default  28.0000  28.0000
6         규모  19193.000000  19193.000000  Default  27.0000  27.0000
183       시장  33157.000000  33157.000000  Default  26.0000  26.0000
...      ...           ...           ...      ...      ...      ...
10302    블로그      0.003571      1.416456  Topic40 -10.3373   4.7601
10303  삼풍백화점      0.003571      1.416456  Topic40 -10.3373   4.7601
10304     서사      0.003571      1.416456  Topic40 -10.3373   4.7601
10305   성수대교      0.003571      1.416456  Topic40 -10.3373   4.7601
10278     마법      0.003571      1.416456  Topic40 -10.3373   4.7601

[1898 rows x 6 columns], token_table=      Topic      Freq  Term
term                       
315       1  0.946984    가격
315      17  0.009599    가격
315      37  0.043329    가격
2277     19  0.997539    가계
2014     16  0.994952  가계부채
...     ...       ...   ...
68       13  0.449959    흡수
68       14  0.549085    흡수
1800      5  0.644343    희망
1800     30  0.355333    희망
1478     26  0.993451    희생

[2195 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[26, 24, 31, 21, 8, 16, 2, 15, 3, 32, 33, 39, 13, 5, 40, 22, 19, 25, 35, 10, 17, 38, 11, 34, 1, 29, 18, 28, 6, 9, 23, 20, 14, 4, 30, 27, 36, 12, 37, 7])